# Usage

## Dependencies

You will need to install the following dependencies:

```
brew install awscli kubectl helm
```

## Authentication

Ensure you have access to EKS which is done by adding your IAM to the EKS in the
terraform configuration.

```
KUBECONFIG=./kubeconfig aws --profile=account eks update-kubeconfig --cluster cluster-name
```

There can be multiple clusters so pick the correct cluster.  Ensure that you set
`export KUBECONFIG=./kubeconfig` to get the correct `KUBECONFIG` file. This can
be added into you .bashrc or .zshrc

## Ingress

The ingress is in its simplest form a Kubernetes LoadBalancer. Instead of what
would traditionally be this:

``` sh
DNS (i.e app.example.com) -> Kubernetes Service -> Kubernetes Pods
```

It is the following

``` sh
DNS (i.e app.example.com) -> Ingress (Public IP Address/CNAME) -> Kubernetes Service -> Kubernetes Pods
```

To break down the Ingress request cycle even further it is the following:

``` sh
DNS (i.e app.example.com) -> Ingress [Kubernetes Service -> Kubernetes Pods (Nginx) -> Kubernetes Service -> Kubernetes Pods]
```

The Ingress is just another pod such as Nginx that relays the traffic and as
such is just another pod in the system. The ingress is a helm chart and is
installed manually with the following script.

The ingress works at the DNS layer so it needs to be passed a Host to work:

``` sh
curl -k -H "Host: app.example.com" <https://a54313f35cb5b11e98bb60231b063008-2077563408.us-west-2.elb.amazonaws.com>
```


## Deployments

### Scale Down / Up

This has to be done through the deployment in the helm chart. Another way to do it is to scale down

```
num=0

kubectl scale --replicas=${num} -n <namespace> deployment/<deploymentname>
```

## Pods

### List Running Pods

``` sh
kubectl get pods -A
```

Kubernetes lets you divide your cluster into namespaces. Each namespace can have
its own set of resources. The above command lists all running pods on every
cluster. Pods in the kube-system namespace belong to Kubernetes and helps it
function.

### Describe Pods

```
kubectl describe pods <podname>
```

### “SSH”

To connect to the application look at the namespaces:

``` sh
kubectl get pods -A
kubectl exec -it -n <namespace> <pod> -c <container> -- bash
```


### Logs

``` sh
kubectl get pods -A
kubectl logs -f -n <namespace> <pod> -c <container>
```

This lets you view the logs of the running pod. The container running on the pod
should be configured to output logs to STDOUT/STDERR.


### Restart a Pod

If you pod is not responding or needs a restart the way to do it is to use the
following command. This will delete the pod and replace it with a new pod if it
is a part of a deployment.

```
kubectl delete pod <pod-name>
```

### Pod Issues

A pod can have various different errors. The common ones are:

 - OOMError: The pod or underlying node ran out of memory and killed the pod.
 - CrashLoopBackup: The application itself has an issue, use `kubectl logs -f <pod>` to find out why
 - ImageNotFound: The docker image for the pod can't be found.

